In [67]:
# from google.colab import drive
# drive.mount('/content/drive')

In [68]:
import warnings
warnings.filterwarnings('ignore')

In [69]:
import os
import glob
import seisbench.models as sbm
from obspy import read, read_events
from obspy import UTCDateTime as utc
import sys
import pickle
from datetime import datetime as dt
import logging
import pandas as pd
import numpy as np

In [70]:
from obspy.signal.trigger import recursive_sta_lta, trigger_onset
from seisbench.util.annotations import Pick, PickList, ClassifyOutput
class stalta:
    def __init__(self, sta, lta, on, off):
        self.name = 'STALTA'
        self.sta = sta
        self.lta = lta
        self.trigger_on = on
        self.trigger_off = off
    def classify(self, stream):
        output = ClassifyOutput('STALTA')
        picks = PickList()
        st = stream.select(channel='*Z')
        for tr in st:
            sps = tr.stats.sampling_rate
            sta_sample = int(self.sta * sps)
            lta_sample = int(self.lta * sps)
            cft = recursive_sta_lta(tr.data, sta_sample, lta_sample)
            # plot_trigger(tr, cft, trigger_on, trigger_of)
            lst_on_of = trigger_onset(cft, self.trigger_on, self.trigger_off)
            for on_of in lst_on_of:
                pick_time = start_time =  tr.stats.starttime + (on_of[0]/sps)
                end_time = tr.stats.starttime + (on_of[1]/sps)
                pick = Pick(trace_id='.'.join(tr.id.split('.')[:-1]),
                            start_time=start_time,
                            end_time=end_time,
                            peak_time=pick_time,
                            peak_value=on_of[0],
                            phase='P')
                picks.append(pick)
        output.picks = picks
        return output

In [71]:
# gdrive_path = '/content/drive/MyDrive'
# path = f'{gdrive_path}/Colab Notebooks/PhD-Thesis_ImanKahbasi'
# sys.path.append(path)
###
import MyFuncs as mf
from MyFuncs.structure import Result

In [72]:
# gdrive_dir = '/content/drive/MyDrive'
# colab_dir = f'{gdrive_dir}/Colab Notebooks'
# working_dir = f'{colab_dir}/PhD-Thesis_ImanKahbasi'
working_dir = '.'
data_dir = f'{working_dir}/IIEES_2006-2023'

In [73]:
fileObjPath = f'{data_dir}/eventid_waveformpath.pickle_OBJ'
eventid_waveformpath = {}

lst_waveform_dirs = glob.glob(f'{data_dir}/Waveforms/*')
for indx, path in enumerate(lst_waveform_dirs):
    eventid = os.path.basename(path).replace('waveform', '')
    path_waveform = mf.funcs.get_iiees_stream_path(path)
    # print(path_waveforms)
    # print(indx, eventid, path_waveform)
    eventid_waveformpath[eventid] = path_waveform
output = open(fileObjPath, 'wb')
pickle.dump(eventid_waveformpath, output)
output.close()
################################################################################
# fileObjPath = f'{data_dir}/eventid_waveformpath.pickle_OBJ'
# with open(fileObjPath, 'rb') as pickle_file:
#     eventid_waveformpath0 = pickle.load(pickle_file)
# eventid_waveformpath = eventid_waveformpath0

In [74]:
###
# eventid_waveformpath = {k: eventid_waveformpath0[k] for k in list(eventid_waveformpath0.keys())[:5]}
###
# for k, v in eventid_waveformpath.items():
#     print(k, v)

In [75]:
# path = "/home/ekarkooti/Documents/JSEE/SeisBench-JSEE_1402-08-16/IIEES_2006-2023/BIN_2004_2024-Cleaned.out"
# f = open(path)
# cat = read_events(f)
# print(cat)
# # cat = read_events('/home/ekarkooti/Documents/JSEE/SeisBench-JSEE_1402-08-16/IIEES_2018-2023/2018-2023_origin.out')

In [76]:
cat = read_events(f'{data_dir}/BIN_2004_2024-Cleaned.out')
Details_lst_filenames = glob.glob(f'{data_dir}/Details/*')


KeyboardInterrupt: 

In [ ]:
eventid2catalog = mf.funcs.eventid2catalog(Details_lst_filenames, cat)

In [ ]:
len(eventid2catalog)

861

In [ ]:
proccessing_mode = 'CPU'
DPDN = False # Deep-DeNoiser

In [ ]:
if DPDN:
    model_dnoise = sbm.DeepDenoiser.from_pretrained('original')
    if proccessing_mode == 'GPU':
        model_dnoise.cuda()

## Define models

### Download and cash all models

In [ ]:
# lst_models = ['BasicPhaseAE', 'PhaseNet', 'EQTransformer', 'GPD']

# for model_name in lst_models:
#     exec(f"model = sbm.{model_name}")
#     lst = model.list_pretrained()
#     for pretrained in lst:
#         print(model_name, pretrained)
#         exec(f"model2 = model.from_pretrained('{pretrained}')")
#         print('Done')

In [ ]:
time_name = utc().strftime('%Y%m%dT%H%M%S')
root_output = f'{working_dir}/DL-picks-results_{time_name}'
os.makedirs(root_output, exist_ok=True)

In [ ]:
time_name

'20240220T105202'

### Make a list of target models that we want to apply on data

In [ ]:
# df_models = pd.read_csv('stalta-tunning.csv', comment='#')
# df_models['model'] = None
# for indx, row in df_models.iterrows():
#     df_models.at[indx, 'model'] = stalta(sta=row.sta,
#                                          lta=row.lta,
#                                          on=row.on,
#                                          off=row.off)

In [ ]:
# for indx, row in df_models.iterrows():
#     print(row.model.sta, row.model.lta)

In [ ]:
meta_header = ['eventid', 'wavename',
               'execution_time', 'RunTimeEQ',
               'freqmin', 'freqmax', 'DPDN',
               'picker_name', 'training_data', 'detection_threshold',
               'sta', 'lta', 'on', 'off']

In [ ]:
columns = ['picker_name', 'training_data', 'processor', 'freqmin', 'freqmax',
           'sta', 'lta', 'on', 'off', 'model']
lst_models = []
low_corner_filter  = [None, 1, 1,  1,  0.5, 0.5, 0.5, 2, 2,  2]
high_corner_filter = [None, 8, 10, 12, 8,   10,  12,  8, 10, 12]
for freqmin, freqmax in zip(low_corner_filter, high_corner_filter):
    for sta in [0.5, 1, 2, 3]:
        for lta in [5, 10, 15, 20]:
            for on in [3, 4, 5, 7, 9]:
                for off in [0.5, 0.7, 1]:
                    model = stalta(sta=sta,
                                lta=lta,
                                on=on,
                                off=off)
                    model_row = ['STALTA', 'energy', 'CPU', freqmin, freqmax,
                                 sta, lta, on, off, model]
                    lst_models.append(model_row)
df_models = pd.DataFrame(lst_models, columns=columns)

In [ ]:
df_models

picker_name training_data processor  freqmin  freqmax  sta  lta  on  off  \
0         STALTA        energy       CPU      NaN      NaN  0.5    5   3  0.5   
1         STALTA        energy       CPU      NaN      NaN  0.5    5   3  0.7   
2         STALTA        energy       CPU      NaN      NaN  0.5    5   3  1.0   
3         STALTA        energy       CPU      NaN      NaN  0.5    5   4  0.5   
4         STALTA        energy       CPU      NaN      NaN  0.5    5   4  0.7   
...          ...           ...       ...      ...      ...  ...  ...  ..  ...   
2395      STALTA        energy       CPU      2.0     12.0  3.0   20   7  0.7   
2396      STALTA        energy       CPU      2.0     12.0  3.0   20   7  1.0   
2397      STALTA        energy       CPU      2.0     12.0  3.0   20   9  0.5   
2398      STALTA        energy       CPU      2.0     12.0  3.0   20   9  0.7   
2399      STALTA        energy       CPU      2.0     12.0  3.0   20   9  1.0   

                                           model  
0     <__main__.stalta object at 0x7fb9f0ac1a80>  
1     <__main__.stalta object at 0x7fb9f0951090>  
2     <__main__.stalta object at 0x7fb9f0ac0b80>  
3     <__main__.stalta object at 0x7fb9f0ac1720>  
4     <__main__.stalta object at 0x7fb9f0ac3ac0>  
...                                          ...  
2395  <__main__.stalta object at 0x7fb9f083a050>  
2396  <__main__.stalta object at 0x7fb9f083a0b0>  
2397  <__main__.stalta object at 0x7fb9f083a110>  
2398  <__main__.stalta object at 0x7fb9f083a170>  
2399  <__main__.stalta object at 0x7fb9f083a1d0>  

[2400 rows x 10 columns]

## Processing data

In [79]:
time_name = utc().strftime('%Y%m%dT%H%M%S')
root_output = f'{working_dir}/DL-picks-results_{time_name}'
os.makedirs(root_output, exist_ok=True)

In [ ]:
# eventid_waveformpath_2 = {}
# ii = 0
# for eventid, wavepath in eventid_waveformpath.items():
#     eventid_waveformpath_2[eventid] = wavepath
#     ii += 1
#     if ii == 5:
#         break

In [80]:
meta_header = ['eventid', 'wavename',
               'execution_time', 'RunTimeEQ',
               'freqmin', 'freqmax', 'DPDN',
               'picker_name', 'training_data', 'detection_threshold',
               'sta', 'lta', 'on', 'off']

# with open(f'metadata-of-run_{time_name}.csv', 'a') as metaout:
#     metaout.write(','.join(meta_header)+'\n')

ii_t = len(eventid_waveformpath)


for indx, model in df_models.iterrows():
    freqmin = model.freqmin
    freqmax = model.freqmax
    DPDN = False
    picker_name = model.picker_name
    training_data = model.training_data
    detection_threshold = None
    sta = model.sta
    lta = model.lta
    on = model.on
    off = model.off
    print('\n' + '\t'.join([str(_) for _ in model.values[:-1]]))
    root_output2 = f'{root_output}/STALTA_{model.freqmin}-{model.freqmax}_{model.sta}-{model.lta}_{model.on}-{model.off}'
    os.makedirs(root_output2, exist_ok=True)
    ###
    metadata_filename = f'metadata-of-run_{time_name}.csv'
    with open(f'{root_output2}/{metadata_filename}', 'w') as metaout:
        metaout.write(','.join(meta_header)+'\n')

    ii = 0
    for eventid, wavepath in eventid_waveformpath.items():
        if ii == int(ii_t*(10/100)):
            break
        percent=ii/ii_t*100; print(f'{eventid} ({percent:.2f}%)', end='/'); ii += 1
        wavename = os.path.basename(wavepath)
        wavename = wavename.split('.')[0][:-1]
        #
        st = read(wavepath)
        st.merge(-1)
        st.detrend('constant')
        st.merge(fill_value=0)
        st.resample(100)
        for tr in st:
            tr.stats.network = 'BI'
            tr.stats.channel = tr.stats.channel.replace(' ', 'H')
        ### filtering
        if not np.isnan(model.freqmin) or not np.isnan(model.freqmax):
            print('Bandpss Filter')
            st.filter('bandpass', freqmin=model.freqmin, freqmax=model.freqmax,
                      zerophase=True)
        sRunTimeEQ = dt.now()
        classified = model.model.classify(st)
        eRunTimeEQ = dt.now()
        RunTimeEQ = (eRunTimeEQ - sRunTimeEQ).total_seconds()
        ### write results in an output file
        execution_time = sRunTimeEQ.strftime('%Y%m%dT%H%M%S')
        
        pickle_name = f'eID-{eventid}_wID-{wavename}_{model.picker_name}_{execution_time}.pickle'
        with open(f'{root_output2}/{pickle_name}', 'wb') as outfile:
            pickle.dump(classified.picks, outfile)
        ###
        picker_name = model.picker_name
        training_data = model.training_data
        sta = model.sta
        lta = model.lta
        on = model.on
        off = model.off
        # detection_threshold = model.model.
        with open(f'{root_output2}/metadata-of-run_{time_name}.csv', 'a') as metaout:
            meta = []
            for _ in meta_header:
                try:
                    meta.append(str(eval(_)))
                except:
                    meta.append('None')
            metaout.write(','.join(meta)+'\n')


STALTA	energy	CPU	nan	nan	0.5	5	3	0.5
65349 (0.00%)/65692 (0.12%)/67740 (0.23%)/63025 (0.35%)/109076 (0.47%)/64815 (0.58%)/103465 (0.70%)/65468 (0.81%)/65293 (0.93%)/109213 (1.05%)/62118 (1.16%)/64357 (1.28%)/109378 (1.40%)/109497 (1.51%)/33348 (1.63%)/105033 (1.74%)/33382 (1.86%)/2338 (1.98%)/110564 (2.09%)/67977 (2.21%)/62453 (2.33%)/65479 (2.44%)/106598 (2.56%)/38365 (2.67%)/63614 (2.79%)/109134 (2.91%)/67918 (3.02%)/63549 (3.14%)/63426 (3.26%)/106052 (3.37%)/38551 (3.49%)/63042 (3.60%)/39536 (3.72%)/102983 (3.84%)/65608 (3.95%)/2207 (4.07%)/63030 (4.19%)/65973 (4.30%)/56955 (4.42%)/107241 (4.53%)/66655 (4.65%)/58515 (4.77%)/34613 (4.88%)/64805 (5.00%)/107285 (5.12%)/107133 (5.23%)/108577 (5.35%)/103186 (5.47%)/64574 (5.58%)/65630 (5.70%)/108801 (5.81%)/102072 (5.93%)/108940 (6.05%)/110247 (6.16%)/64822 (6.28%)/103722 (6.40%)/42276 (6.51%)/108781 (6.63%)/108500 (6.74%)/62530 (6.86%)/14626 (6.98%)/67846 (7.09%)/33474 (7.21%)/108717 (7.33%)/38577 (7.44%)/109873 (7.56%)/108625 (7.67%)